<a href="https://colab.research.google.com/github/sedatoner/Object-Recognition-System-with-YOLOv8/blob/main/Object_Recognition_System_with_YOLOv8.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from ultralytics import YOLO
model = YOLO('yolov8n.pt')

#Setting up the DeepSORT tracker this will help me keep track of objects across frames
from deep_sort_realtime.deepsort_tracker import DeepSort
tracker = DeepSort(max_age=30)

#Uploading a video file from my computer I'll pick a .mp4 file
from google.colab import files
uploaded = files.upload()

import cv2
import numpy as np

#Grabbing the path of the video I just uploaded
video_path = list(uploaded.keys())[0]
cap = cv2.VideoCapture(video_path)

#Getting some basic video properties: width, height, and FPS
width  = int(cap.get(3))
height = int(cap.get(4))
fps = int(cap.get(5))

#Setting up the output video writer this is where I'll save the tracked result
out = cv2.VideoWriter('tracked_output.mp4', cv2.VideoWriter_fourcc(*'mp4v'), fps, (width, height))

#Looping through the video frame by frame
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

# Running YOLO on the current frame (no verbose output)
    results = model(frame, verbose=False)[0]
    detections = []

#Converting YOLO detections into a format that DeepSORT understands
    for r in results.boxes.data.tolist():
        x1, y1, x2, y2, score, class_id = r
        detections.append(([x1, y1, x2 - x1, y2 - y1], score, str(int(class_id))))

# Feeding the detections to the tracker
    tracks = tracker.update_tracks(detections, frame=frame)

#Drawing the results: bounding boxes + object IDs
    for track in tracks:
        if not track.is_confirmed():
            continue
        track_id = track.track_id
        l, t, r, b = track.to_ltrb()
        cv2.rectangle(frame, (int(l), int(t)), (int(r), int(b)), (0, 255, 0), 2)
        cv2.putText(frame, f'ID {track_id}', (int(l), int(t - 10)), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255,255,255), 2)

# Writing the annotated frame to the output video
    out.write(frame)

#Done with everything closing video files
cap.release()
out.release()
print("Takip tamamlandı! Video: tracked_output.mp4")

# Let's take a look at the result right here in Colab
from IPython.display import Video
Video("tracked_output.mp4", embed=True)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 19.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 45.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 88.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 67.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 38.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 76.3 MB/s eta 0:00:00
Creating new Ultralytics Settings v0.0.6 file ✅ 


100%|██████████| 6.25M/6.25M [00:00<00:00, 77.0MB/s]


Saving background video _ people _ walking _.mp4 to background video _ people _ walking _.mp4
✅ Takip tamamlandı! Video: tracked_output.mp4


In [4]:
from google.colab import files
files.download("tracked_output.mp4")


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>